In [281]:
import glob
from bs4 import BeautifulSoup
import re
from tqdm import tqdm
import pandas as pd
from datetime import datetime, timedelta
import calendar
from collections import Counter
import requests
import multiprocessing as mp
from multiprocessing import Pool
import time
from datetime import datetime

# WEB CRAWL
import urllib
import random
import datetime as dt
from itertools import cycle

## Functions

In [4]:
def convert_date(date):
    # Remove special characters
    date = re.sub('[^a-z0-9]', " ", date)
    try:
        # ASSUMING dd MMM
        # Extract day
        day_start = re.search('^\d+', date).start()
        day_end = re.search('^\d+', date).end()
        day = date[day_start:day_end]
        if len(day) == 1:
            day = "0"+day
        # Extract month
        date_wo_day = date[day_end:].strip()
        month_start = re.search('^\w+', date_wo_day).start()
        month_end = re.search('^\w+', date_wo_day).end()
        month = date_wo_day[month_start:month_end]
        if "jan" in str(month):
            month = "01"
        if "feb" in str(month):
            month = "02"
        if "mar" in str(month):
            month = "03"
        if "apr" in str(month):
            month = "04"
        if "may" in str(month):
            month = "05"
        if "jun" in str(month):
            month = "06"
        if "jul" in str(month):
            month = "07"
        if "aug" in str(month):
            month = "08"
        if "sep" in str(month):
            month = "09"
        if "oct" in str(month):
            month = "10"
        if "nov" in str(month):
            month = "11"
        if "dec" in str(month):
            month = "12"

        full_date = day+"."+month+".2019"
        if len(full_date) == 10:
            return datetime.strptime(full_date, '%d.%m.%Y').date()
        else:
            return "nil"
    except:
        return "nil"

In [12]:
def convert_time(time, post_time):
    return_time = "nil"
    time_original = str(re.sub(r'[.:]', '', time)).strip()
    time_original = str(re.sub(r'^([a-zA-Z]+ ){1,}', '', time_original)).strip()
    time_original = str(re.sub(r'\d+\-', '', time_original)).strip()
    
    # ASSUME NUM PM
    if bool(re.search(r'^\d+ ?pm', time_original)):
        time = time_original.replace("pm", "").strip()
        time = str(time)
        # If 1,2,3,4,5,6,7,8,9
        if len(str(time)) == 1:
            time = int(time)
            if time == 1:
                return_time = "13:00"
            if time == 2:
                return_time = "14:00"
            if time == 3:
                return_time = "15:00"
            if time == 4:
                return_time = "16:00"
            if time == 5:
                return_time = "17:00"
            if time == 6:
                return_time = "18:00"
            if time == 7:
                return_time = "19:00"
            if time == 8:
                return_time = "20:00"
            if time == 9:
                return_time = "21:00"
        # If 10,11,12
        if len(str(time)) == 2:
            time = int(time)
            if time == 10:
                return_time = "22:00"
            if time == 11:
                return_time = "23:00"
            if time == 12:
                return_time = "12:00"
        # If single hour (eg. 1) and minutes (eg. 15)
        if len(str(time)) == 3:
            hour = int(time[0])
            if hour == 1:
                return_time = "13:"+time[1:]
            if hour == 2:
                return_time = "14:"+time[1:]
            if hour == 3:
                return_time = "15:"+time[1:]
            if hour == 4:
                return_time = "16:"+time[1:]
            if hour == 5:
                return_time = "17:"+time[1:]
            if hour == 6:
                return_time = "18:"+time[1:]
            if hour == 7:
                return_time = "19:"+time[1:]
            if hour == 8:
                return_time = "20:"+time[1:]
            if hour == 9:
                return_time = "21:"+time[1:]
        # If double hour (eg. 11) and minutes (eg. 30)
        if len(str(time)) == 4:
            hour = int(time[0:2])
            if hour == 10:
                return_time = "22:"+time[2:]
            if hour == 11:
                return_time = "23:"+time[2:]
            if hour == 12:
                return_time = "12:"+time[2:]
    
    # ASSUME NUM AM
    if bool(re.search(r'^\d+ ?am', time_original)):
        time = time_original.replace("am", "").strip()
        time = str(time)
        # If 1,2,3,4,5,6,7,8,9
        if len(str(time)) == 1:
            time = int(time)
            if time == 1:
                return_time = "01:00"
            if time == 2:
                return_time = "02:00"
            if time == 3:
                return_time = "03:00"
            if time == 4:
                return_time = "04:00"
            if time == 5:
                return_time = "05:00"
            if time == 6:
                return_time = "06:00"
            if time == 7:
                return_time = "07:00"
            if time == 8:
                return_time = "08:00"
            if time == 9:
                return_time = "09:00"
        # If 10,11,12
        if len(str(time)) == 2:
            time = int(time)
            if time == 10:
                return_time = "10:00"
            if time == 11:
                return_time = "11:00"
            if time == 12:
                return_time = "00:00"
        # If single hour (eg. 1) and minutes (eg. 15)
        if len(str(time)) == 3:
            hour = int(time[0])
            if hour == 1:
                return_time = "01:"+time[1:]
            if hour == 2:
                return_time = "02:"+time[1:]
            if hour == 3:
                return_time = "03:"+time[1:]
            if hour == 4:
                return_time = "04:"+time[1:]
            if hour == 5:
                return_time = "05:"+time[1:]
            if hour == 6:
                return_time = "06:"+time[1:]
            if hour == 7:
                return_time = "07:"+time[1:]
            if hour == 8:
                return_time = "08:"+time[1:]
            if hour == 9:
                return_time = "09:"+time[1:]
        # If double hour (eg. 11) and minutes (eg. 30)
        if len(str(time)) == 4:
            hour = int(time[0:2])
            if hour == 10:
                return_time = "10:"+time[2:]
            if hour == 11:
                return_time = "11:"+time[2:]
            if hour == 12:
                return_time = "00:"+time[2:]
    
    # ASSUME NO PM OR AM
    if bool(re.search(r'^\d+$', time_original)):
        time = str(time_original).strip()
        # If single digit
        if len(time) == 1:
            time = int(time)
            post_hour = post_time[:2]
            if int(post_hour) >= 12:
                if time == 1:
                    return_time = "13:00"
                if time == 2:
                    return_time = "14:00"
                if time == 3:
                    return_time = "15:00"
                if time == 4:
                    return_time = "16:00"
                if time == 5:
                    return_time = "17:00"
                if time == 6:
                    return_time = "18:00"
                if time == 7:
                    return_time = "19:00"
                if time == 8:
                    return_time = "20:00"
                if time == 9:
                    return_time = "21:00"
            else:
                if time == 1:
                    return_time = "01:00"
                if time == 2:
                    return_time = "02:00"
                if time == 3:
                    return_time = "03:00"
                if time == 4:
                    return_time = "04:00"
                if time == 5:
                    return_time = "05:00"
                if time == 6:
                    return_time = "06:00"
                if time == 7:
                    return_time = "07:00"
                if time == 8:
                    return_time = "08:00"
                if time == 9:
                    return_time = "09:00"
        # If double digits
        if len(str(time)) == 2:
            time = int(time)
            post_hour = post_time[:2]
            if int(post_hour) >= 12:
                if time == 10:
                    return_time = "22:00"
                if time == 11:
                    return_time = "23:00"
                if time == 12:
                    return_time = "12:00"
            else:
                if time == 10:
                    return_time = "10:00"
                if time == 11:
                    return_time = "11:00"
                if time == 12:
                    return_time = "00:00"    
        # If three digtis
        if len(str(time)) == 3:
            hour = int(str(time)[0])
            post_hour = post_time[:2]
            if int(post_hour) >= 12:
                if hour == 1:
                    return_time = "13:"+time[1:]
                if hour == 2:
                    return_time = "14:"+time[1:]
                if hour == 3:
                    return_time = "15:"+time[1:]
                if hour == 4:
                    return_time = "16:"+time[1:]
                if hour == 5:
                    return_time = "17:"+time[1:]
                if hour == 6:
                    return_time = "18:"+time[1:]
                if hour == 7:
                    return_time = "19:"+time[1:]
                if hour == 8:
                    return_time = "20:"+time[1:]
                if hour == 9:
                    return_time = "21:"+time[1:]
            else:
                if hour == 1:
                    return_time = "01:"+time[1:]
                if hour == 2:
                    return_time = "02:"+time[1:]
                if hour == 3:
                    return_time = "03:"+time[1:]
                if hour == 4:
                    return_time = "04:"+time[1:]
                if hour == 5:
                    return_time = "05:"+time[1:]
                if hour == 6:
                    return_time = "06:"+time[1:]
                if hour == 7:
                    return_time = "07:"+time[1:]
                if hour == 8:
                    return_time = "08:"+time[1:]
                if hour == 9:
                    return_time = "09:"+time[1:]
        # If four digtis
        if len(str(time)) == 4:
            hour = int(str(time)[0:2])
            post_hour = post_time[:2]
            if int(post_hour) >= 12:
                if hour >= 12:
                    return_time = str(hour)+":"+str(time)[2:]
                if hour == 10:
                    return_time = "22:"+time[2:]
                if hour == 11:
                    return_time = "23:"+time[2:]
                if hour == 0:
                    return_time = "00:"+time[2:]
            else:
                if hour <= 12:
                    if len(str(hour)) == 1:
                        return_time = "0"+str(hour)+":"+str(time)[2:]
                    else:
                        return_time = str(hour)+":"+str(time)[2:]
                if hour == 0:
                    return_time = "00:"+time[2:]
                if hour == 10:
                    return_time = "10:"+time[2:]
                if hour == 11:
                    return_time = "11:"+time[2:]
                if hour == 12:
                    return_time = "00:"+time[2:]
        
    return return_time

## Process Data

### Read Files

In [6]:
html_files_old = glob.glob("./telegram_chat_export_beginning_19sep/*.html")
print("Number of files: ", len(html_files_old))
print(html_files_old[:10])
print()

html_files_new = glob.glob("./telegram_chat_export_13oct_10dec/*.html")
print("Number of files: ", len(html_files_new))
print(html_files_new[:10])

Number of files:  257
['./telegram_chat_export_beginning_19sep\\messages.html', './telegram_chat_export_beginning_19sep\\messages10.html', './telegram_chat_export_beginning_19sep\\messages100.html', './telegram_chat_export_beginning_19sep\\messages101.html', './telegram_chat_export_beginning_19sep\\messages102.html', './telegram_chat_export_beginning_19sep\\messages103.html', './telegram_chat_export_beginning_19sep\\messages104.html', './telegram_chat_export_beginning_19sep\\messages105.html', './telegram_chat_export_beginning_19sep\\messages106.html', './telegram_chat_export_beginning_19sep\\messages107.html']

Number of files:  160
['./telegram_chat_export_13oct_10dec\\messages.html', './telegram_chat_export_13oct_10dec\\messages10.html', './telegram_chat_export_13oct_10dec\\messages100.html', './telegram_chat_export_13oct_10dec\\messages101.html', './telegram_chat_export_13oct_10dec\\messages102.html', './telegram_chat_export_13oct_10dec\\messages103.html', './telegram_chat_export_1

In [7]:
html_files = [*html_files_old, *html_files_new]
print("Total html files: ", len(html_files))

Total html files:  417


### Extract Data from Files

In [64]:
messages_list = []
total_messages = 0

for file in tqdm(html_files):    
    f = open(file, "r", encoding='utf-8')
    chat = f.read()
    soup = BeautifulSoup(chat)
    messages = soup.findAll("div", {"class": "message default clearfix"})
    total_messages += len(messages)

    for message in messages:
        # Get user
        user = message.find("div", {"class": "from_name"}).text.replace("\n", "").strip()
        #print(user)
        # Get post date and time
        post_datetime = message.find("div", {"class": "pull_right date details"}).get("title")
        post_date = post_datetime.split(" ")[0]
        post_time = post_datetime.split(" ")[1]
        #print(post_date)
        #print(post_time)
        # GET MESSAGE
        raw_message = message.find("div", {"class": "text"})
        # Extract text from message
        raw_message = str(raw_message).replace("</div>", "").replace('<div class="text">', "").replace("<strong>", "").replace("</strong>", "").replace("<u>", "").replace("</u>", "").strip().lower()
        # Tokenize text
        raw_message_tokens = re.sub(r'(<br/> ?){2,}', '<br/>', raw_message).split("<br/>")

        # Variable flag for actual ride request
        is_request = False
        # Get user type
        if(bool(re.search(r'hitchers? looking', raw_message_tokens[0]))):
            user_type = "hitcher"
            is_request = True
        elif(bool(re.search(r'driver? looking', raw_message_tokens[0]))):
            user_type = "driver"
            is_request = True
        else:
            user_type = "nil"

        # PROCESS MESSAGE CONTENT IF IT IS ACTUALLY A REQUEST
        if(is_request):
            # Blank place holder
            pick_up = "nil"
            drop_off = "nil"
            request_date = "nil"
            request_time = "nil"
            number_of_pax = "nil"
            request_date_normalised = "nil"
            request_time_normalised = "nil"
            day = "nil"
            # ------------------

            # Extract pick up location assuming it is always the second token
            try:
                pick_up_tokens = str(raw_message_tokens[1]).split(":")
            except:
                pass
            try:
                if "pick" in pick_up_tokens[0]:
                    pick_up = pick_up_tokens[1].strip()
            except:
                pick_up_tokens = str(raw_message_tokens[1]).split(" ")
                if "pick" in pick_up_tokens[0]:
                    pick_up = " ".join(pick_up_tokens[1:])
                else:
                    pass

            # Extract drop off location assuming it is always the third token
            try:
                drop_off_tokens = str(raw_message_tokens[2]).split(":")
            except:
                pass
            try:
                if "drop" in drop_off_tokens[0]:
                    drop_off = drop_off_tokens[1].strip()
            except:
                drop_off_tokens = str(raw_message_tokens[2]).split(" ")
                if "drop" in drop_off_tokens[0]:
                    drop_off = " ".join(drop_off_tokens[1:])
                else:
                    pass

            # Extract date assuming it is always the fourth token
            try:
                date_tokens = str(raw_message_tokens[3]).split(":")
            except:
                pass
            try:
                if "date" in date_tokens[0]:
                    request_date = date_tokens[1].strip()
            except:
                date_tokens = str(raw_message_tokens[3]).split(" ")
                if "date" in date_tokens[0]:
                    request_date = " ".join(date_tokens[1:])
                else:
                    pass
            if "today" in request_date or "tdy" in request_date:
                request_date = datetime.strptime(post_date, '%d.%m.%Y').date()
            elif "tmr" in request_date or "tomorrow" in request_date:
                today_date = datetime.strptime(post_date, '%d.%m.%Y').date()
                tomorrow_date = today_date + timedelta(days=1)
                request_date = tomorrow_date
            elif request_date == "nil":
                pass
            else:
                request_date = convert_date(request_date)
            
            # Extract time assuming it is always the fifth token
            try:
                time_raw = str(raw_message_tokens[4])
            except:
                pass
            try:
                time = time_raw.replace("time:", "").replace("time :", "").strip()
                time = re.sub(r'[^a-z0-9.-:]', '', time).strip()
                if "now" in time:
                    request_time = post_time[:5]
                else:
                    request_time = convert_time(str(time), post_time)
            except:
                pass
                
            # Extract number of pax assuming it is always the sixth token
            try:
                if "pax" in raw_message_tokens[5]:
                    raw_pax = str(raw_message_tokens[5]).replace("pax:", "").replace("pax", "").replace("pax :", "").replace("pax : ", "").strip()
                    raw_pax = raw_pax.replace(":", "").strip()
                    raw_pax = re.sub(r'\(.*\)', '', raw_pax)
                    raw_pax = re.sub(r'[^a-z0-9- ]', '', raw_pax)
                    raw_pax = raw_pax.strip()
                    if len(raw_pax) == 1:
                        number_of_pax = raw_pax
                    elif len(raw_pax) == 3:
                        number_of_pax = raw_pax
                    else:
                        if bool(re.search(r'^\d+ - \d+$', raw_pax)):
                            number_of_pax = raw_pax.replace(" ", "")
                        if bool(re.search(r'^\d+ to \d+$', raw_pax)):
                            number_of_pax = raw_pax.replace("to", "-")
                            number_of_pax = number_of_pax.replace(" ", "")
            except:
                pass
            
            # If request_date and time is "nil" format of message might be wrong
            if request_date == "nil" or request_time == "nil":
                # Extract time again
                try:
                    time_raw = re.search(r'time\:.*\<br\/\>', raw_message).group()
                    time = time_raw.split("<br/>")[0]
                    time = time.replace("time:", "").strip()  
                    if "now" in time:
                        request_time = post_time[:5]
                    else:
                        request_time = convert_time(str(time), post_time)
                except:
                    pass
                # Extract date again
                try:
                    date_raw = re.search(r'date\:.*\<br\/\>', raw_message).group()
                    request_date = date_raw.split("<br/>")[0]
                    request_date = date.replace("date:", "").strip()
                    if "today" in request_date or "tdy" in request_date:
                        request_date = datetime.strptime(post_date, '%d.%m.%Y').date()
                    elif "tmr" in request_date or "tomorrow" in request_date:
                        today_date = datetime.strptime(post_date, '%d.%m.%Y').date()
                        tomorrow_date = today_date + timedelta(days=1)
                        request_date = tomorrow_date
                    else:
                        request_date = convert_date(request_date)
                except:
                    if request_time != "nil":
                        request_date = datetime.strptime(post_date, '%d.%m.%Y').date()
                # Extract pax again
                try:
                    if bool(re.search(r'pax:.*\<br\/\>', raw_message)):
                        raw_pax = re.search(r'pax:.*\<br\/\>', lol).group()
                        raw_pax = raw_pax.split("<br/>")[0]
                        raw_pax = raw_pax.replace("pax:", "").strip()
                    if bool(re.search(r'pax:.*$', lol)):
                        raw_pax = re.search(r'pax:.*$', lol).group()
                        raw_pax = raw_pax.replace("pax:", "").strip()
                except:
                    pass
            
            #--------------------NORMALISE DATA---------------------
            
            # Normalise date and time
            try:
                date_time = datetime.strptime(str(request_date)+" "+request_time, '%Y-%m-%d %H:%M')
                approx = round(date_time.minute/30.0) * 30
                date_time = date_time.replace(minute=0)
                date_time += timedelta(seconds=approx*60)
                request_date_normalised = date_time.date()
                request_time_normalised = date_time.strftime('%H:%M')
            except:
                pass
            
            # Add day to data eg. dd-mm-yyyy = wed
            try:
                my_date = datetime.strptime(str(request_date_normalised), '%Y-%m-%d')
                day = calendar.day_name[my_date.weekday()].lower()
            except:
                pass
            
            # Store structured message into dictionary
            message_data = {
                'user' : user,
                'post_date' : post_date,
                'post_time' : post_time,
                'raw_message' : raw_message,
                'user_type' : user_type,
                'pick_up' : pick_up,
                'drop_off' : drop_off,
                'request_date' : request_date,
                'request_date_normalised' : request_date_normalised,
                'request_time' : request_time,
                'request_time_normalised' : request_time_normalised,
                'day' : day,
                'number_of_pax' : number_of_pax
            }
            messages_list.append(message_data)

100%|████████████████████████████████████████████████████████████████████████████████| 417/417 [05:49<00:00,  1.09it/s]


### Stats

In [65]:
print("Total number of messages: \t\t", total_messages)
print("Total number of actual messages: \t", len(messages_list))
print()
print("Percentage of actual messages: \t", round((len(messages_list)/total_messages)*100, 2), "%")

Total number of messages: 		 376598
Total number of actual messages: 	 360464

Percentage of actual messages: 	 95.72 %


### Convert Data to DataFrame

In [ ]:
data = pd.DataFrame(messages_list)
data.head()
data.to_csv("./data/sg_hitch_data_raw_updated.csv")

### Filter out Corrupted Data

In [56]:
data = pd.read_csv("./data/sg_hitch_data_raw_updated.csv", index_col=0)

# Filter out corrupted request time
clean_data_rt = data[data.request_time_normalised != "nil"]
print("Removed", len(data)-len(clean_data_rt), "corrupted request time")
# Filter out corrupted request date
clean_data_rd = clean_data_rt[clean_data_rt.request_date_normalised != "nil"]
print("Removed", len(clean_data_rt)-len(clean_data_rd), "corrupted request date")
# Filter out corrupted pick up
clean_data_pu = clean_data_rd[clean_data_rd.pick_up != "nil"]
print("Removed", len(clean_data_rd)-len(clean_data_pu), "corrupted pick up")
# Filter out corrupted drop off
clean_data_do = clean_data_pu[clean_data_pu.drop_off != "nil"]
print("Removed", len(clean_data_pu)-len(clean_data_do), "corrupted drop off")

Removed 18292 corrupted request time
Removed 0 corrupted request date
Removed 318 corrupted pick up
Removed 2341 corrupted drop off


In [57]:
clean_data = clean_data_do
print("Number of requests left: ", len(clean_data))
print()
print("Percentage of non-corrupted data: ", round(len(clean_data)/len(data)*100, 2), "%")

Number of requests left:  339513

Percentage of non-corrupted data:  94.19 %


In [58]:
clean_data.head()

day            drop_off number_of_pax                     pick_up  \
1  tuesday     bedok reservoir           nil                   tuas area   
2  tuesday           off - ntu           nil        up - mountbatten mrt   
3  tuesday          north-east           nil  bedok/tamp/pasir ris/eunos   
4  tuesday  north-east or east           nil                      jurong   
7  tuesday                suss           nil                 jurong west   

    post_date post_time                                        raw_message  \
1  26.02.2019  14:55:47  driver looking for hitchers<br/>pick up: tuas ...   
2  26.02.2019  15:00:23  hitcher looking for drivers<br/>pick up - moun...   
3  26.02.2019  15:39:19  driver looking for hitchers<br/>pick up: bedok...   
4  26.02.2019  18:12:47  driver looking for hitchers<br/>pick up: juron...   
7  26.02.2019  23:50:17  hitcher looking for drivers <br/>pick up: juro...   

  request_date request_date_normalised request_time request_time_normalised  \
1   2019-02-26              2019-02-26        18:15                   18:00   
2   2019-02-26              2019-02-26        17:00                   17:00   
3   2019-02-26              2019-02-26        16:00                   16:00   
4   2019-02-26              2019-02-26        18:12                   18:00   
7   2019-02-26              2019-02-26        07:30                   07:30   

                    user user_type  
1                 xoxoxo    driver  
2                 Amanda   hitcher  
3                      J    driver  
4  Colonel Ronald Silver    driver  
7                 a. Lee   hitcher

### Normalise Data

In [327]:
# Clean up pick_up and drop_off
def clean_location(loc):
    # Split multiple nearby locations to use first
    if '/' in loc:
        loc = loc.split('/')[0].strip()
    # Replace short forms
    clean = re.sub(r'\,', ' ', loc)
    clean = re.sub(r'  ', ' ', clean)
    clean = re.sub(r'\(.*\)', '', clean)
    clean = re.sub(r'\bblock\b', '', clean)
    clean = re.sub(r'\bblk\b', '', clean)
    clean = re.sub(r'\bave\b', 'avenue', clean)
    clean = re.sub(r'\bamk\b', 'ang mo kio', clean)
    clean = re.sub(r'\bcck\b', 'choa chu kang', clean)
    clean = re.sub(r'\btpy\b', 'toa payoh', clean)
    clean = re.sub(r'\byck\b', 'yio chu kang', clean)
    clean = re.sub(r'^vivo$', 'vivo city', clean)
    clean = re.sub(r'\btamp\b', 'tampines', clean)
    clean = re.sub(r'\bseng kang\b', 'sengkang', clean)
    clean = re.sub(r'\bcq\b', 'clarke quay', clean)
    clean = re.sub(r'\bwlds\b', 'woodlands', clean)
    clean = re.sub(r'^\bwoodland\b$', 'woodlands', clean)
    clean = re.sub(r'^\bsim\b$', 'singapore institute of management', clean)
    return clean.strip()

pick_up = clean_data['pick_up'].tolist()
drop_off = clean_data['drop_off'].to_list()

pick_up_clean = []
drop_off_clean = []

for pu in tqdm(pick_up):
    pick_up_clean.append(clean_location(str(pu)))
    
for do in tqdm(drop_off):
    drop_off_clean.append(clean_location(str(do)))



  0%|          | 0/339513 [00:00<?, ?it/s]

  2%|▏         | 7025/339513 [00:00<00:04, 70248.39it/s]

  5%|▍         | 15522/339513 [00:00<00:04, 74099.71it/s]

  7%|▋         | 23734/339513 [00:00<00:04, 76334.74it/s]

  9%|▉         | 32082/339513 [00:00<00:03, 78345.57it/s]

 12%|█▏        | 40522/339513 [00:00<00:03, 80067.52it/s]

 14%|█▍        | 48762/339513 [00:00<00:03, 80753.24it/s]

 17%|█▋        | 57092/339513 [00:00<00:03, 81500.22it/s]

 19%|█▉        | 65612/339513 [00:00<00:03, 82574.79it/s]

 22%|██▏       | 73809/339513 [00:00<00:03, 82391.02it/s]

 24%|██▍       | 81780/339513 [00:01<00:03, 80193.91it/s]

 26%|██▋       | 89921/339513 [00:01<00:03, 80553.85it/s]

 29%|██▉       | 98162/339513 [00:01<00:02, 81099.31it/s]

 31%|███▏      | 106659/339513 [00:01<00:02, 82221.23it/s]

 34%|███▍      | 114981/339513 [00:01<00:02, 82517.95it/s]

 36%|███▋      | 123363/339513 [00:01<00:02, 82902.80it/s]

 39%|███▉      | 131683/339513 [00:01<00:02, 82989.63it/s]

 41%|██

In [328]:
print(Counter(pick_up_clean).most_common(20))
print()
print(Counter(drop_off_clean).most_common(20))

[('woodlands', 9954), ('yishun', 8363), ('sengkang', 7836), ('tampines', 7721), ('punggol', 6209), ('hougang', 5962), ('choa chu kang', 5758), ('ang mo kio', 5457), ('pasir ris', 5396), ('jurong west', 4222), ('bedok', 3943), ('jurong', 3648), ('sembawang', 3282), ('bukit batok', 3260), ('bukit panjang', 2997), ('clarke quay', 2168), ('town', 2021), ('toa payoh', 1910), ('serangoon', 1788), ('clementi', 1728)]

[('anywhere', 9975), ('woodlands', 9225), ('yishun', 7934), ('tampines', 7282), ('sengkang', 7088), ('hougang', 5967), ('punggol', 5943), ('choa chu kang', 5623), ('ang mo kio', 5218), ('pasir ris', 4927), ('jurong west', 3968), ('jurong', 3748), ('bedok', 3691), ('bukit panjang', 3039), ('town', 2933), ('sembawang', 2925), ('bukit batok', 2845), ('clementi', 1910), ('toa payoh', 1824), ('serangoon', 1709)]


In [116]:
# Check if values change
for i in range(5004,5010):
    print("Org: ", pick_up[i])
    print("Clean: ", pick_up_clean[i])
    print()

Org:  wlds 731628
Clean:  woodlands 731628

Org:  star vista
Clean:  star vista

Org:  jurong
Clean:  jurong

Org:  760236
Clean:  760236

Org:  jurong east/bukit batok
Clean:  jurong east

Org:  vivo
Clean:  vivo city



In [335]:
# Add columns to dataframe
data_normalised = clean_data.assign(pick_up_clean=pick_up_clean,
                                    drop_off_clean=drop_off_clean,
                                    pick_up_geo="nil",
                                    drop_off_geo="nil")
data_normalised.head()

day            drop_off number_of_pax                     pick_up  \
1  tuesday     bedok reservoir           nil                   tuas area   
2  tuesday           off - ntu           nil        up - mountbatten mrt   
3  tuesday          north-east           nil  bedok/tamp/pasir ris/eunos   
4  tuesday  north-east or east           nil                      jurong   
7  tuesday                suss           nil                 jurong west   

    post_date post_time                                        raw_message  \
1  26.02.2019  14:55:47  driver looking for hitchers<br/>pick up: tuas ...   
2  26.02.2019  15:00:23  hitcher looking for drivers<br/>pick up - moun...   
3  26.02.2019  15:39:19  driver looking for hitchers<br/>pick up: bedok...   
4  26.02.2019  18:12:47  driver looking for hitchers<br/>pick up: juron...   
7  26.02.2019  23:50:17  hitcher looking for drivers <br/>pick up: juro...   

  request_date request_date_normalised request_time request_time_normalised  \
1   2019-02-26              2019-02-26        18:15                   18:00   
2   2019-02-26              2019-02-26        17:00                   17:00   
3   2019-02-26              2019-02-26        16:00                   16:00   
4   2019-02-26              2019-02-26        18:12                   18:00   
7   2019-02-26              2019-02-26        07:30                   07:30   

                    user user_type         pick_up_clean      drop_off_clean  \
1                 xoxoxo    driver             tuas area     bedok reservoir   
2                 Amanda   hitcher  up - mountbatten mrt           off - ntu   
3                      J    driver                 bedok          north-east   
4  Colonel Ronald Silver    driver                jurong  north-east or east   
7                 a. Lee   hitcher           jurong west                suss   

  pick_up_geo drop_off_geo  
1         nil          nil  
2         nil          nil  
3         nil          nil  
4         nil          nil  
7         nil          nil

In [340]:
# Get location that are not planning area names
df = pd.read_csv("./data/planning_area_population.csv")
planning_areas = df['name'].tolist()

data_no_pa = data_normalised[~data_normalised['pick_up_clean'].isin(planning_areas)]

data_no_pa_final = data_no_pa[~data_no_pa['drop_off_clean'].isin(planning_areas)]

print("Length: ", len(data_no_pa_final))
print()
data_no_pa_final.head()

Length:  188209



day              drop_off number_of_pax                    pick_up  \
1     tuesday       bedok reservoir           nil                  tuas area   
2     tuesday             off - ntu           nil       up - mountbatten mrt   
4     tuesday    north-east or east           nil                     jurong   
13  wednesday  paya lebar or nearby           nil                 plaza sing   
21  wednesday              parklane           nil  changi airport terminal 1   

     post_date post_time                                        raw_message  \
1   26.02.2019  14:55:47  driver looking for hitchers<br/>pick up: tuas ...   
2   26.02.2019  15:00:23  hitcher looking for drivers<br/>pick up - moun...   
4   26.02.2019  18:12:47  driver looking for hitchers<br/>pick up: juron...   
13  27.02.2019  08:33:33  driver looking for hitchers<br/>pick up: plaza...   
21  27.02.2019  12:39:01  hitcher looking for driver <br/>pick up: chang...   

   request_date request_date_normalised request_time request_time_normalised  \
1    2019-02-26              2019-02-26        18:15                   18:00   
2    2019-02-26              2019-02-26        17:00                   17:00   
4    2019-02-26              2019-02-26        18:12                   18:00   
13   2019-02-27              2019-02-27        08:33                   08:30   
21   2019-02-27              2019-02-27        14:00                   14:00   

                     user user_type              pick_up_clean  \
1                  xoxoxo    driver                  tuas area   
2                  Amanda   hitcher       up - mountbatten mrt   
4   Colonel Ronald Silver    driver                     jurong   
13              Geraldine    driver                 plaza sing   
21                 我是小肥 💛   hitcher  changi airport terminal 1   

          drop_off_clean pick_up_geo drop_off_geo  
1        bedok reservoir         nil          nil  
2              off - ntu         nil          nil  
4     north-east or east         nil          nil  
13  paya lebar or nearby         nil          nil  
21              parklane         nil          nil

In [314]:
#from fake_useragent import UserAgent
#ua = UserAgent()
#HEADER = {'User-Agent': ua.random}
HEADERS_LIST = [
    'Mozilla/5.0 (Windows; U; Windows NT 6.1; x64; fr; rv:1.9.2.13) Gecko/20101203 Firebird/3.6.13',
    'Mozilla/5.0 (compatible, MSIE 11, Windows NT 6.3; Trident/7.0; rv:11.0) like Gecko',
    'Mozilla/5.0 (Windows; U; Windows NT 6.1; rv:2.2) Gecko/20110201',
    'Opera/9.80 (X11; Linux i686; Ubuntu/14.10) Presto/2.12.388 Version/12.16',
    'Mozilla/5.0 (Windows NT 5.2; RW; rv:7.0a1) Gecko/20091211 SeaMonkey/9.23a1pre'
]

PROXY_URL = 'https://free-proxy-list.net/'

def get_proxies():
    response = requests.get(PROXY_URL)
    soup = BeautifulSoup(response.text, 'lxml')
    table = soup.find('table',id='proxylisttable')
    list_tr = table.find_all('tr')
    list_td = [elem.find_all('td') for elem in list_tr]
    list_td = list(filter(None, list_td))
    list_ip = [elem[0].text for elem in list_td]
    list_ports = [elem[1].text for elem in list_td]
    list_proxies = [':'.join(elem) for elem in list(zip(list_ip, list_ports))]
    return list_proxies

In [323]:
# Get lat-long of location pick_up_clean and drop_off_clean
def get_address(row_index):
    time.sleep(0.1)
    #-----PARAMETERS------
    HEADER = {'User-Agent': random.choice(HEADERS_LIST)}
    proxy = next(proxy_pool)
    #---------------------
    
    pick_up_geo = "nil"
    drop_off_geo = "nil"
    
    if bool(re.search(r'\d{6}', data_normalised.iloc[row_index]['pick_up_clean'])):
        pu_location = re.search(r'\d{6}', data_normalised.iloc[row_index]['pick_up_clean']).group()
    else:
        pu_location = data_normalised.iloc[row_index]['pick_up_clean']
    onemap_url = "https://developers.onemap.sg/commonapi/search"
    onemap_params = {'searchVal' : pu_location, 'returnGeom' : "Y", 'getAddrDetails' : "Y"}
    r = requests.get(url = onemap_url, params = onemap_params, headers=HEADER, proxies={"http": proxy}, timeout=60)
    data = r.json()
    try:
        lat = data['results'][0]['LATITUDE']
        long = data['results'][0]['LONGTITUDE']
        lat_long = lat+","+long
        pick_up_geo = lat_long
    except:
        pass
    
    if bool(re.search(r'\d{6}', data_normalised.iloc[row_index]['drop_off_clean'])):
        do_location = re.search(r'\d{6}', data_normalised.iloc[row_index]['drop_off_clean']).group()
    else:
        do_location = data_normalised.iloc[row_index]['drop_off_clean']
    onemap_params = {'searchVal' : do_location, 'returnGeom' : "Y", 'getAddrDetails' : "Y"}
    r = requests.get(url = onemap_url, params = onemap_params, headers=HEADER, proxies={"http": proxy}, timeout=60)
    data = r.json()
    try:
        lat = data['results'][0]['LATITUDE']
        long = data['results'][0]['LONGTITUDE']
        lat_long = lat+","+long
        drop_off_geo = lat_long
    except:
        pass
    
    print(row_index, pu_location, pick_up_geo, do_location, drop_off_geo)
    return pd.DataFrame([[row_index, pu_location, pick_up_geo, do_location, drop_off_geo]], columns=['index', 'pick_up_loc', 'pick_up_geo', 'drop_off_loc', 'drop_off_geo'])

In [325]:
proxies = get_proxies()
proxy_pool = cycle(proxies)

start = datetime.now()
with Pool(15) as p:
    result = p.map(get_address, range(len(data_normalised)-1))
print("time: ", datetime.now()-start)

data_geocode = pd.concat(result)
data_geocode.head()

56590 yishun 1.41694678230154,103.845000884876 ecp 1.2977230348875801,103.90137805264798
28295 ubi 1.32719134796668,103.899109366532 bedok 1.32368201682055,103.947789319297
45272 bedok 1.32368201682055,103.947789319297 sembawang 1.4505243561844299,103.829006229545
39613 marsling mrt nil hillview bukit panjang nil
33954 650405 1.36576439078244,103.74539925546699 760259 1.4349800635856598,103.83896471860001
67908 481 sembawang drive 1.45248404456572,103.81541042056601 orchid hotel 1.2769035925169099,103.843854230672
0 tuas area nil bedok reservoir 1.34231030001047,103.925857758506
11318 punggol 1.40546002750829,103.898354203231 aranda country club 1.3761056770853999,103.953517403291
62249 serangoon 1.3448920150304198,103.87125222941201 pasir ris 1.3799565415449098,103.96361889803002
73567 northstar @ ang mo kio 1.37792345550022,103.87538983402399 ubi techpark 1.32659397595727,103.896139897973
22636 singapore poly 1.3078779264449798,103.7795746708 ang mo kio 1.3687783887791,103.8402739443

33960 clementi 1.2963298251589699,103.7676022071 tiong bahru 1.28188236723141,103.830663094413
11323 520449 1.35702424225034,103.951054363893 461044 1.32901430131172,103.925667777871
22642 ite college central 1.37820943389009,103.85647269130399 tiong bahru 1.28188236723141,103.830663094413
56596 serangoon 1.3448920150304198,103.87125222941201 ngee ann city 1.30242417189412,103.83467612472299
79232 rivertrees residences(fernvale close) nil kranji camp 2 nil
39619 sengkang 1.38315380470819,103.89238167637801 temasek polytechnic 1.34675551907396,103.929081571971
62255 telok ayer ( beer factory) nil 734788 1.4439158188000603,103.802554333627
5665 bedok mall 1.3246689739690902,103.92940545649 tp 1.34465891016166,103.932313181851
45278 sengkang 1.38315380470819,103.89238167637801 15a surin ave 1.35465576055611,103.880337363687
50937 ubi 1.32719134796668,103.899109366532 punggol 1.40546002750829,103.898354203231
67914 sembawang 1.4505243561844299,103.829006229545 yishun 1.41694678230154,103.8

73578 680562 1.39629871036487,103.746022677229 centrepoint 1.30197804548976,103.839758893141
79237 yishun 1.41694678230154,103.845000884876 geylang or town area nil
50942 tuas naval base 1.29496117231452,103.663730121406 boon lay 1.3480815464086202,103.70817710905001
28306 jurong west 1.34160326621595,103.70808518963301 east 1.3108349867393,103.92171580265999
16988 thomson 1.3180924884862402,103.844767904553 sembawang 1.4505243561844299,103.829006229545
11 clementi 1.2963298251589699,103.7676022071 bedok 1.32368201682055,103.947789319297
56602 westgate pick up point nil 161 yung ping rd 1.32977632869249,103.721585931129
5671 530165 1.35025425918973,103.887795306397 520943 1.35017819018821,103.941193548918
39625 city square mall (farrer park) nil 730016 1.44229782292057,103.77787852047899
62261 565 thomson road 1.33876450783753,103.83682258924999 560106 1.3719337032349,103.83748606185101
22649 clementi 1.2963298251589699,103.7676022071 bangkit 1.3775072762462,103.77360557644
67920 semba

33972 toa payoh 1.33904144822194,103.857955654132 bishan 1.3596538482492302,103.832637290371
79243 white sands 1.37239898072244,103.949749226457 786471 1.4044675173932701,103.821333688649
28312 changi business park 1.3382574839696,103.96704967897301 thomson plaza 1.35432524209243,103.83032810292801
17 121a edgedale plains 1.3940023463568703,103.90862829324301 tampines hub 1.35310120216274,103.940848647333
56608 yishun 1.41694678230154,103.845000884876 ecp 1.2977230348875801,103.90137805264798
45289 yishun 1.41694678230154,103.845000884876 tanah merah d manor 1.3304260990746102,103.94640003907
16994 sengkang 1.38315380470819,103.89238167637801 ascott raffles place 1.2820845546650401,103.851544398473
62267 565 thomson road 1.33876450783753,103.83682258924999 560106 1.3719337032349,103.83748606185101
73585 commonwealth 1.29556628401854,103.806204356557 cathay 1.30924090828304,103.919408618888
39631 821661 1.40303056639258,103.917080721325 760123 1.4345726394731497,103.831796919201
67926 5

22660 plaza sing 1.37976754317117,103.93620756732099 730640 1.43807796920963,103.80238657562401
45295 752510 1.453608954893,103.820883631768 153075 1.28902314290104,103.816276016167
79249 suss 1.3136407681546398,103.790065521402 simpang bedok 1.33367770451888,103.945745989689
11341 730748 1.44533476577032,103.795414343244 680012 1.37946433280775,103.755671539991
56614 tampines 1.35022823751066,103.928412800091 punggol 1.40546002750829,103.898354203231
73590 680562 1.39629871036487,103.746022677229 centrepoint 1.30197804548976,103.839758893141
5683 sengkang 1.38315380470819,103.89238167637801 jurong east 1.34063904358364,103.742474504127
23 pasir ris  tampines  simei  bedok nil anywhere nil
28318 ubi 1.32719134796668,103.899109366532 bedok 1.32368201682055,103.947789319297
67932 changi jewel 1.36033174518933,103.989670344538 bishan 1.3596538482492302,103.832637290371
33979 cash studio nil jurong 1.34390440884759,103.766254087753
22661 changi naval base 1.3167647013931,104.02178247804301

...

254663 188westwood avenue nil jcube 1.33323785085839,103.740191321438
192413 toa payoh lor 1 1.3412382069252902,103.846389510905 holiday inn atrium 1.28907019285004,103.83406828285
209391 sengkang 1.38315380470819,103.89238167637801 kult yard nil
186756 yishun 1.41694678230154,103.845000884876 tampines 1.35022823751066,103.928412800091
220709 esplanade mall 1.28950956232932,103.855665761542 nautical condo sembawang nil
243345 woodlands 808 st 81 1.4422812397851301,103.78691557368 eastpoint mall 1.3425864408894,103.95307233895399
203732 boon keng mrt 1.31923205626252,103.86189339354999 320075 1.32441875533383,103.858185074994
181096 lot 1 1.38506836476439,103.744950378815 park avenue 1.2922274828545202,103.840399301717
215051 570265 1.3583123798758798,103.842088235009 the grounds at kranji nil
226369 woodlands 1.41520591465648,103.758554325238 618274 1.3265335983440902,103.72598107101
232027 senoko crescent 1.4628712360811897,103.80674179017299 woodlands 1.41520591465648,103.75855432523

260328 bukit panjang 1.3775072762462,103.77360557644 eunos 1.3185160978872401,103.905352746532
249010 river valley 1.29596366531643,103.837820229312 anywhere nil
226374 sengkang 1.38315380470819,103.89238167637801 town 1.30923241301234,103.842649053422
181102 bukit batok 1.36053358595052,103.74236455589701 toh guan road 1.33671239134924,103.747614187224
203738 tampines central 1.35518565295547,103.94592520100599 100 am mall nil
186762 ang mo kio 1.3687783887791,103.840273944362 yishun 1.41694678230154,103.845000884876
220715 jurong east 1.34063904358364,103.742474504127 ang mo kio 1.3687783887791,103.840273944362
254670 188westwood avenue nil jcube 1.33323785085839,103.740191321438
198080 choa chu kang 1.4038469560746203,103.749878668123 pandan valley 1.31954451439578,103.77860811204701
260329 sengkang 1.38315380470819,103.89238167637801 tampines abacus plaza 1.3527033076639399,103.94289455022499
237692 northpoint 1.4262604363921498,103.83626143358299 jewel changi airport 1.36033174518

209403 400320 1.32880527103035,103.904280456723 singapore institute of management 1.32913701690828,103.776185827202
215062 expo hall 3 1.33312234827571,103.95901363186199 bukit panjang mrt 1.3790158787748101,103.761921007838
220721 treehouse villa 1.3910587057511001,103.982763416602 3 location nil
186768 670469 1.3878892574394899,103.77328787892 changi airport terminal 2 departure 1.3562397543598301,103.98936496626
249016 clementi 1.2963298251589699,103.7676022071 sembawang 1.4505243561844299,103.829006229545
254676 bukit batok 1.3508238085532098,103.73826825406601 tampines 1.35022823751066,103.928412800091
203744 orchid country club 1.41110357649476,103.844214479132 sembawang shopping centre 1.4418532534675101,103.824832416105
198086 750118 1.4448019498765001,103.829424693375 228095 1.3020840794266,103.849621716147
232039 tanah merah ferry terminal 1.3122633998891,103.988211916284 yishun street 51 1.41635818578282,103.843433570637
226381 prinsep 1.29970274449064,103.849886983698 pasir

192431 lucky plaza 1.30446378974741,103.834005158524 530106 1.3537029714401103,103.890680792553
209409 bukit panjang 1.3775072762462,103.77360557644 bali lane 1.3011646450568601,103.85837752864401
198092 sengkang 1.38315380470819,103.89238167637801 jurong east 1.34063904358364,103.742474504127
237703 choa chu kang 1.4038469560746203,103.749878668123 45 amoy street (telok ayer) 1.2804158588697099,103.846971528547
254682 clementi 1.2963298251589699,103.7676022071 bedok 1.32368201682055,103.947789319297
181114 simei 1.337313178397,103.95136942172701 bugis area nil
220727 520370 1.3580388536739099,103.959670086702 820138 1.39277115890645,103.90979621369699
249022 woodlands blk 700+ nil ang mo kio ite 1.3772444788381601,103.856431219196
243362 punggol 1.40546002750829,103.898354203231 jurong imm 1.33491758755438,103.74687713286801
215069 republic polytechnic 1.44496816514051,103.78536240689199 changi city point 1.3340363790270802,103.96291761553101
203750 sengkang 1.38315380470819,103.89238

JSONDecodeError: Expecting value: line 1 column 1 (char 0)

In [326]:
data_geocode

NameError: name 'data_geocode' is not defined

In [ ]:
data_geocode.to_csv("./data/sg_hitch_data_geocode.csv")